# Задача
Необходимо создать модель, которая будет предсказывать стоимость автомобиля по его характеристикам. Для оценки использовать метрику MAPE

С помощью данного ноутбука был проведен сбор данных с помощью парсинга для обучения.

В этом проекте использовали: Ноутбук, через который парсили https://www.kaggle.com/igorchernov/sf-dst-car-price-parser

Спарсенный датасет https://www.kaggle.com/igorchernov/input/data-car-sales/

Ноутбук, в котором провели EDA https://www.kaggle.com/igorchernov/sf-dst-car-price-eda

Ноутбук, в котором провели обучение https://www.kaggle.com/igorchernov/sf-dst-car-price-ml

In [1]:
import pandas as pd
import os
import requests
from bs4 import BeautifulSoup
import csv
import re
import glob
import json
import concurrent.futures
import time
import datetime

In [2]:
import warnings 
warnings.filterwarnings("ignore") 

In [3]:
_debug_mode = False

# Функции для парсинга

In [4]:
# функция получения страницы по адресу

def get_page(url):
    #headers = {'user-agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/89.0.4389.114 Safari/537.36', 'Cookie': '_csrf_token=e06ec3b4cac26954499a25d7a651baca0cb09dfe3f13be90; autoru_gdpr=1; autoruuid=g6066406e2k99ttmc5t5ladjk4aif7r7.c902643577af5e4f51d7218fc1fddd7f; suid=d3ae225d6b7f58d77e0faf5501c45f89.76ffd8381b3c3f209a7ac40e8e5ef0ba; yuidlt=1; yandexuid=9266985931608033188; my=YwA=; gdpr=0; _ym_uid=1617313903102348004; listing_view_session={}; autoru_sid=a:g6066406e2k99ttmc5t5ladjk4aif7r7.c902643577af5e4f51d7218fc1fddd7f|1617918702051.604800.nqu_KnagaSJ5L8T4V_-u9g.bvcge8gBjTOxGZ3-ZSojsTkz1tOVzf47pl3q0KcJvMU; X-Vertis-DC=vla; _ym_isad=2; gids=225; listing_view={"output_type":"table","version":1}; autoru-visits-count=2; autoru-visits-session-unexpired=1; from=other; _ym_d=1617913472; from_lifetime=1617913472696; cycada=/tGSgvkfuQovrGbiPr9JRwTgF3/yZiJBexlRLUSI20U='
    #           }
    
    response = requests.get(url)#, headers=headers)
    response.encoding = 'utf8'
    return BeautifulSoup(response.text, 'html.parser')

In [5]:
# функция получения списка марок автомобилей

def get_brand_links():
    
    url = f'https://auto.ru'
    soup_main = get_page(url)

    all_brand_links = []

    for brand in soup_main.find_all('a', class_='IndexMarks__item'):
        all_brand_links.append(brand.get('href').replace('all', 'used'))

    return all_brand_links

In [6]:
# функция проверки числа объявлений

def check_number(url):
    
    strr = 'ButtonWithLoader__content'
    page = get_page(url)
    cntt = page.find(class_=strr).text.split(' ')[1].split('\xa0')
    if len(cntt[1]) > 3:
        cnt = int(cntt[0])
    else:
        cnt = int(cntt[0]+cntt[1])
    return cnt

In [7]:
# функция получения списка адресов со страницы со списком

def get_page_car_links(page_url):
    
    page = get_page(page_url)
    if page == None:
        return []
    all_link = page.find_all(class_='ListingItemTitle__link')
    links = []
    for link in all_link:
        links.append(link['href'])
    return links

In [8]:
# функция получения списка адресов

def get_car_links(url):

    try:
        strr = 'ListingPagination__page'
        max_page = int(get_page(url).find_all(class_=strr)[-1].text)
    except:
        max_page = 0

    links = []

    if _debug_mode:
        if max_page:
            max_page = 1
    
    if max_page:
        page_urls = [url + '?page=' + str(i) for i in range(1, max_page + 1)]

        with concurrent.futures.ThreadPoolExecutor() as executor:
            futures = []
            for url in page_urls:
                futures.append(executor.submit(get_page_car_links, page_url=url))
            for feature in concurrent.futures.as_completed(futures):
                links += feature.result()
    return links

In [10]:
# функция получения списка ссылок на все объявления по заданной марке

def get_links(brand_links):
    car_type = ['sedan', 'hatchback', 'allroad', 'wagon',
                'coupe', 'minivan', 'pickup', 'limousine', 'van', 'cabrio']
    car_links = []
    for link in brand_links:
        time.sleep(0.01)
        cnt = check_number(link)
        if cnt <= 3700:
            car_links += get_car_links(link)
        else:
            for year in range(1999, 2022):
                if year > 2000:
                    aa = link.split('/')
                    url_1 = '/'.join(aa[:5])+'/'+str(year)+'-year/used/'
                else:
                    url_1 = link+'?year_to=2000'
                cnt = check_number(url_1)
                if cnt <= 3700:
                    car_links += get_car_links(url_1)
                else:
                    for cb in car_type:
                        if year > 2000:
                            url_2 = url_1+f'body-{cb}/'
                        else:
                            url_2 = link+f'body-{cb}/?year_to=2000'
                        car_links += get_car_links(url_2)
                        
    return car_links

In [11]:
# функция получения списка ссылок на все объявления по заданной марке

# def get_links(brand_links):
    
#     car_links = []
#     for link in brand_links:
#         time.sleep(0.01)
#         car_links += get_car_links(link)
#     return car_links

In [12]:
# функция получения данных с одной страницы

def get_car_info(car_link):
    
    soup_car = get_page(car_link)
    car_info = {}
    cls_str = 'CardInfoRow_'
    span_str = 'CardInfoRow__cell'
#    regex = re.compile('.*__info-item.*')
    regex = re.compile('CardHead__infoItem.*')
    sd = 'sale-data-attributes'
    
    if soup_car.find('div', class_='CardSold') == None:

        car_info['datetime'] = datetime.datetime.now(
            datetime.timezone(datetime.timedelta(hours=3)))
        car_info['parsing_unixtime'] = int(time.time())
        car_info['card'] = soup_car.find(
            'div', class_='CardSidebarActions__title').text
        car_info['region'] = soup_car.find(
            'span', class_='MetroListPlace__regionName MetroListPlace_nbsp').text
        if soup_car.find('div', class_='CardSellerNamePlace__name'):
            car_info['sellerName'] = soup_car.find(
                'div', class_='CardSellerNamePlace__name').text
        elif soup_car.find('a', class_='CardSellerNamePlace__name_dealer'):
            car_info['dealerName'] = soup_car.find(
                'a', class_='CardSellerNamePlace__name_dealer').text
        car_info['sell_id'] = soup_car.find(
            'div', title='Идентификатор объявления').text
        car_info['car_url'] = car_link
        car_info['price'] = soup_car.find(
            'span', class_='OfferPriceCaption__price').text
        car_info['description'] = soup_car.find(
            'div', class_='CardDescription__textInner').text
        car_info['image'] = 'https:' + \
            soup_car.find(
                'img', class_='ImageGalleryDesktop__image').get('src')

        soup_name = soup_car.find(
            'div', class_='CardBreadcrumbs').find_all('a')

        car_info['bodyType'] = soup_car.find(
            'li', class_=cls_str+'bodytype').find('a').text
        car_info['color'] = soup_car.find(
            'li', class_=cls_str+'color').find('a').text
        car_info['engine'] = soup_car.find(
            'li', class_=cls_str+'engine').find('div').text
        car_info['engineDisplacement'], car_info['enginePower'], car_info['fuelType'] = car_info['engine'].split(
            '/')
        car_info['mileage'] = soup_car.find(
            'li', class_=cls_str+'kmAge').find_all('span')[1].text
        car_info['productionDate'] = soup_car.find(
            'li', class_=cls_str+'year').find_all('span')[1].text
        car_info['vehicleTransmission'] = soup_car.find(
            'li', class_=cls_str+'transmission').find_all('span')[1].text
        car_info['Владельцы'] = soup_car.find(
            'li', class_=cls_str+'ownersCount').find_all('span')[1].text
        car_info['ПТС'] = soup_car.find(
            'li', class_=cls_str+'pts').find_all('span')[1].text
        car_info['Привод'] = soup_car.find(
            'li', class_=cls_str+'drive').find_all('span')[1].text
        car_info['Руль'] = soup_car.find(
            'li', class_=cls_str+'wheel').find_all('span')[1].text
        car_info['Состояние'] = soup_car.find(
            'li', class_=cls_str+'state').find_all('span')[1].text
        car_info['Таможня'] = soup_car.find(
            'li', class_=cls_str+'customs').find_all('span')[1].text
        car_info['card_type'] = soup_name[1].text
        car_info['brand'] = soup_name[2].text
        car_info['model_name'] = soup_name[3].text
        car_info['model_name2'] = soup_name[4].text
        car_info['name'] = soup_name[6].text
        car_info['equipment_dict'] = sale_data = json.loads(
            soup_car.find(id=sd)['data-bem'])[sd]

        car_info['public_date'] = soup_car.find_all(
            'div', {"class": regex})[0].text
        car_info['nview'] = soup_car.find_all('div', {"class": regex})[
            1].text.split(' ')[0]
        car_info['model_name_full'] = soup_car.find('h1').text
        url_2 = soup_car.find('a', class_='SpoilerLink')['href']
        pag = get_page(url_2)
        car_info['confDict'] = json.loads(pag.find(id=sd)['data-bem'])[sd]

#         car_info['complectation_dict'] = soup_car.find_all('div', class_ = 'ComplectationGroups')
#         car_info['equipment_dict'] =
#         car_info['modelDate'] =
#         car_info['model_info'] =
#         car_info['super_gen'] =
#         car_info['vehicleConfiguration'] =
#         car_info['numberOfDoors'] =
#         car_info['vendor'] =
    else:
        car_info = {}

    return car_info

In [13]:
# функция получения данных по дипазону адресов

def get_data(urls):
    
    data = []
    with concurrent.futures.ThreadPoolExecutor() as executor:
        future_to_url = {executor.submit(
            get_car_info, url): url for url in urls}
        for future in concurrent.futures.as_completed(future_to_url):
            url = future_to_url[future]
            try:
                data.append(future.result())
            except Exception as exc:
                print('%r generated an exception: %s' % (url, exc))
    return data

In [14]:
br = get_brand_links()

In [15]:
res_dict = {}

In [16]:
for link in br:
    print(link, check_number(link))
    threaded_start = time.time()
    brand = link.split('/')[4]
    try:
        res_dict[brand] = get_links([link])
    except:
        res_dict[brand]=[]
    print("Load time:", time.time() - threaded_start)

https://auto.ru/cars/vaz/used/ 49001
Load time: 131.83274126052856
https://auto.ru/cars/audi/used/ 7822
Load time: 99.03422713279724
https://auto.ru/cars/bmw/used/ 12288
Load time: 100.95253038406372
https://auto.ru/cars/chery/used/ 2028
Load time: 5.97092866897583
https://auto.ru/cars/chevrolet/used/ 11075
Load time: 95.60724401473999
https://auto.ru/cars/citroen/used/ 1848
Load time: 4.0103864669799805
https://auto.ru/cars/daewoo/used/ 3230
Load time: 3.8335134983062744
https://auto.ru/cars/ford/used/ 10959
Load time: 99.34394550323486
https://auto.ru/cars/geely/used/ 1241
Load time: 5.004413843154907
https://auto.ru/cars/honda/used/ 4873
Load time: 102.05147767066956
https://auto.ru/cars/hyundai/used/ 15460
Load time: 103.13800740242004
https://auto.ru/cars/infiniti/used/ 1465
Load time: 4.222027778625488
https://auto.ru/cars/kia/used/ 15421
Load time: 101.25192666053772
https://auto.ru/cars/land_rover/used/ 2971
Load time: 6.78122878074646
https://auto.ru/cars/lexus/used/ 3403
Load

In [17]:
cnt = 0
for k in res_dict.keys():
    print(k,len(res_dict[k]))
    cnt += len(res_dict[k])
cnt

vaz 1102
audi 870
bmw 873
chery 38
chevrolet 758
citroen 38
daewoo 38
ford 798
geely 38
honda 757
hyundai 873
infiniti 38
kia 872
land_rover 38
lexus 38
lifan 38
mazda 833
mercedes 872
mitsubishi 835
nissan 836
opel 645
peugeot 38
porsche 38
renault 873
skoda 874
ssang_yong 38
subaru 38
suzuki 38
toyota 1254
volkswagen 873
volvo 38
gaz 38
zaz 38
uaz 790


16196

In [18]:
# преобразование полученных данных в датасет

car_link_df = pd.DataFrame(res_dict.items(), columns=['Brand', 'Link'])
car_link_df = car_link_df.explode("Link", ignore_index = True)
car_link_df

Brand                                               Link
0       vaz  https://auto.ru/cars/used/sale/vaz/2107/110525...
1       vaz  https://auto.ru/cars/used/sale/vaz/vesta/11050...
2       vaz  https://auto.ru/cars/used/sale/vaz/2107/110523...
3       vaz  https://auto.ru/cars/used/sale/vaz/2170/110486...
4       vaz  https://auto.ru/cars/used/sale/vaz/2115/110422...
...     ...                                                ...
16191   uaz  https://auto.ru/cars/used/sale/uaz/patriot/110...
16192   uaz  https://auto.ru/cars/used/sale/uaz/patriot/110...
16193   uaz  https://auto.ru/cars/used/sale/uaz/patriot/110...
16194   uaz  https://auto.ru/cars/used/sale/uaz/patriot/110...
16195   uaz  https://auto.ru/cars/used/sale/uaz/patriot/110...

[16196 rows x 2 columns]

In [19]:
# запись в файл

car_link_df.to_csv(os.path.join(os.getcwd(), 'Input/get_car_links.csv'), sep=';', encoding='utf-8', index=False)

In [20]:
car_link_df.iloc[0,1]

'https://auto.ru/cars/used/sale/vaz/2107/1105254242-2fbac2ed/'

In [21]:
# Пример извлечения данных по отдельному авто

car_info = get_car_info(car_link_df.iloc[0,1])

In [22]:
car_info

{'datetime': datetime.datetime(2021, 9, 19, 8, 26, 18, 186573, tzinfo=datetime.timezone(datetime.timedelta(seconds=10800))),
 'parsing_unixtime': 1632029178,
 'card': 'LADA (ВАЗ) 2107 1982-2012',
 'region': 'Москва',
 'sellerName': 'Александр',
 'sell_id': '№ 1105254242',
 'car_url': 'https://auto.ru/cars/used/sale/vaz/2107/1105254242-2fbac2ed/',
 'price': '235\xa0000\xa0₽',
 'description': 'Машина в отличном состоянии, всё работает как положено салон чистый пробег настоящий постоянно в одних руках гаражного хранения.Всё заводское,есть вмятина на заднем крыле смотрите на фото,гнили и ржавчины нет вообще.Все вопросы по телефону или при встрече,звонить только заинтересованным людям у которых есть данная сумма денег.При осмотре есть небольшой торг звонить с 8 до 22.',
 'image': 'https://autoru.naydex.net/13OsZK248/2d52bb7Kmm3D/cFhuiQ3TiCeIGGhvDViFLPraA6RV7V6LpitaMAQ3C3b6i_rL2fW1uv5neJsEIZT2RZBZ7R5D27L5kIHfWzppNgQNP41cZj3z-Xy4KxgN8a0bv8flpX78PWQoKIIGNM3VCJrfb7wEUY448bhs8qXzYdD1D7s-tmt3uzYV

In [23]:
car_info.keys()

dict_keys(['datetime', 'parsing_unixtime', 'card', 'region', 'sellerName', 'sell_id', 'car_url', 'price', 'description', 'image', 'bodyType', 'color', 'engine', 'engineDisplacement', 'enginePower', 'fuelType', 'mileage', 'productionDate', 'vehicleTransmission', 'Владельцы', 'ПТС', 'Привод', 'Руль', 'Состояние', 'Таможня', 'card_type', 'brand', 'model_name', 'model_name2', 'name', 'equipment_dict', 'public_date', 'nview', 'model_name_full', 'confDict'])

In [24]:
# получение данных по ссылкам
car_info_data = get_data(car_link_df['Link'])

'https://auto.ru/cars/used/sale/vaz/2111/1105322475-ec8e6ae0/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/vaz/2115/1105299503-73c769a1/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/vaz/2114/1105308743-dc328b97/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/vaz/2105/1105290877-ea85980a/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/vaz/2115/1105280383-0259a39e/' generated an exception: 'NoneType' object is not subscriptable
'https://auto.ru/cars/used/sale/vaz/2115/1105323972-bd294d2c/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/vaz/2114/1105227159-7400f14a/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/vaz/kalina/1105261960-dfe48cc2/' generated an exception: 'NoneType' 

'https://auto.ru/cars/used/sale/hyundai/grand_starex/1105314729-c44d3248/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/hyundai/grand_starex/1105306394-14351ecc/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/hyundai/ix35/1105313360-c1b00a8f/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/hyundai/h_1_starex/1105323322-9dca59f3/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/hyundai/solaris/1105170257-c6348a34/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/hyundai/solaris/1105317879-cfdceab0/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/hyundai/kona/1105259708-ebf19297/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/infiniti/

'https://auto.ru/cars/used/sale/mitsubishi/lancer/1105146150-c53c046f/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/mitsubishi/pajero_sport/1105281530-55b75544/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/mitsubishi/pajero_sport/1105287964-e3a6d6de/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/mitsubishi/pajero_sport/1105318049-9ef8ceeb/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/nissan/bluebird_sylphy/1105319996-44e60b5c/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/nissan/primera/1105324456-afb28cdc/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/nissan/presage/1105316420-885d9750/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/

'https://auto.ru/cars/used/sale/toyota/land_cruiser/1104972598-ec04b86c/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/toyota/rav_4/1105283634-a327fa6d/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/toyota/land_cruiser_prado/1105283633-61108cee/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/toyota/fortuner/1105283632-03b652f4/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/toyota/hilux/1105283637-e097f296/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/volkswagen/golf/1105324112-686ea7d1/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/volkswagen/golf/1105324112-686ea7d1/' generated an exception: 'NoneType' object has no attribute 'text'
'https://auto.ru/cars/used/sale/volkswag

In [25]:
car_info_data

[{'datetime': datetime.datetime(2021, 9, 19, 8, 26, 29, 6428, tzinfo=datetime.timezone(datetime.timedelta(seconds=10800))),
  'parsing_unixtime': 1632029189,
  'card': 'LADA (ВАЗ) 2107 1982-2012',
  'region': 'Москва',
  'sellerName': 'Александр',
  'sell_id': '№ 1105254242',
  'car_url': 'https://auto.ru/cars/used/sale/vaz/2107/1105254242-2fbac2ed/',
  'price': '235\xa0000\xa0₽',
  'description': 'Машина в отличном состоянии, всё работает как положено салон чистый пробег настоящий постоянно в одних руках гаражного хранения.Всё заводское,есть вмятина на заднем крыле смотрите на фото,гнили и ржавчины нет вообще.Все вопросы по телефону или при встрече,звонить только заинтересованным людям у которых есть данная сумма денег.При осмотре есть небольшой торг звонить с 8 до 22.',
  'image': 'https://autoru.naydex.net/13OsZK248/2d52bb7Kmm3D/cFhuiQ3TiCeIGGhvDViFLPraA6RV7V6LpitaMAQ3C3b6i_rL2fW1uv5neJsEIZT2RZBZ7R5D27L5kIHfWzppNgQNP41cZj3z-Xy4KxgN8a0bv8flpX78PWQoKIIGNM3VCJrfb7wEUY448bhs8qXzYdD1D7s-

In [26]:
cars_df = pd.DataFrame(car_info_data)

In [27]:
cars_df

datetime  parsing_unixtime  \
0     2021-09-19 08:26:29.006428+03:00      1.632029e+09   
1     2021-09-19 08:26:28.557579+03:00      1.632029e+09   
2     2021-09-19 08:26:28.820911+03:00      1.632029e+09   
3     2021-09-19 08:26:28.697239+03:00      1.632029e+09   
4     2021-09-19 08:26:29.587587+03:00      1.632029e+09   
...                                ...               ...   
15970 2021-09-19 09:41:06.027762+03:00      1.632034e+09   
15971 2021-09-19 09:41:06.473824+03:00      1.632034e+09   
15972 2021-09-19 09:41:06.325972+03:00      1.632034e+09   
15973 2021-09-19 09:41:06.850841+03:00      1.632034e+09   
15974 2021-09-19 09:41:07.490142+03:00      1.632034e+09   

                             card           region    sellerName  \
0       LADA (ВАЗ) 2107 1982-2012           Москва     Александр   
1       LADA (ВАЗ) 2115 1997-2012        Ессентуки  Частное лицо   
2       LADA (ВАЗ) 2105 1979-2011  Санкт-Петербург  Частное лицо   
3             LADA (ВАЗ) Priora I      Нижняя Тура  Частное лицо   
4       LADA (ВАЗ) 2106 1976-2006           Липецк  Частное лицо   
...                           ...              ...           ...   
15970  УАЗ Patriot I Рестайлинг 3   Новокуйбышевск        Тамара   
15971  УАЗ Patriot I Рестайлинг 3             Елец        Виктор   
15972  УАЗ Patriot I Рестайлинг 3   Металлплощадка           NaN   
15973  УАЗ Patriot I Рестайлинг 3           Тамбов           NaN   
15974  УАЗ Patriot I Рестайлинг 3            Пенза           NaN   

            sell_id                                            car_url  \
0      № 1105254242  https://auto.ru/cars/used/sale/vaz/2107/110525...   
1      № 1104223543  https://auto.ru/cars/used/sale/vaz/2115/110422...   
2      № 1105129425  https://auto.ru/cars/used/sale/vaz/2105/110512...   
3      № 1104867059  https://auto.ru/cars/used/sale/vaz/2170/110486...   
4      № 1105201652  https://auto.ru/cars/used/sale/vaz/2106/110520...   
...             ...                                                ...   
15970  № 1103647131  https://auto.ru/cars/used/sale/uaz/patriot/110...   
15971  № 1105314023  https://auto.ru/cars/used/sale/uaz/patriot/110...   
15972  № 1105081458  https://auto.ru/cars/used/sale/uaz/patriot/110...   
15973  № 1105000955  https://auto.ru/cars/used/sale/uaz/patriot/110...   
15974  № 1105065012  https://auto.ru/cars/used/sale/uaz/patriot/110...   

             price                                        description  \
0        235 000 ₽  Машина в отличном состоянии, всё работает как ...   
1        155 000 ₽  СРОЧНО!!!! Машина в отличном состоянии для сво...   
2         30 000 ₽  Продам на ходу требует вн мание кузов ездить м...   
3        265 000 ₽  Продаётся Приора. Перебрали этим летом абсолют...   
4         63 000 ₽  Авто в отличном для своих лет состоянии!дно по...   
...            ...                                                ...   
15970    920 000 ₽  Автомобиль 2019г в отличном состоянии, цвет се...   
15971  1 200 000 ₽  Автомобиль в отличном состоянии. Всё то у у ди...   
15972    879 000 ₽  Данный автомобиль продается дилером автомобиле...   
15973  1 400 000 ₽  Автосалон "Глобус" Официальный дилер марки "УА...   
15974  1 380 000 ₽  Продажа от официального дилерского центра ООО ...   

                                                   image  ...       brand  \
0      https://autoru.naydex.net/13OsZK248/2d52bb7Kmm...  ...  LADA (ВАЗ)   
1      https://avatars.mds.yandex.net/get-autoru-vos/...  ...  LADA (ВАЗ)   
2      https://autoru.naydex.net/13OsZK248/2d52bb7Kmm...  ...  LADA (ВАЗ)   
3      https://autoru.naydex.net/13OsZK248/2d52bb7Kmm...  ...  LADA (ВАЗ)   
4      https://avatars.mds.yandex.net/get-autoru-vos/...  ...  LADA (ВАЗ)   
...                                                  ...  ...         ...   
15970  https://avatars.mds.yandex.net/get-autoru-vos/...  ...         УАЗ   
15971  https://avatars.mds.yandex.net/get-verba/10303...  ...         УАЗ   
15972  https://autoru.naydex.net/

In [28]:
# запись в файл примера собранного датафрейма
# в реальности датасет собирался по брэндам авто для минимизации времени парсинга данных

cars_df.to_csv(os.path.join(os.getcwd(), 'Input/cars_data.csv'), sep=';', encoding='utf-8', index=False)

# Вывод
1. Много данных парсится очень долго, пришлось запускать параллельно. Даже обход и сбор ссылок на объявления затратен по времени
2. На авто ру объявления бывают разных типов (с разной разметкой)
3. В данном модуле был приведен пример парсинга. В реальности сбор данных проводился на нескольких станциях и по отдельным маркам авто